In [249]:
# todo 
# 1. Newton and BFGS understand and make table to compare results 
# 2. high level software architecture. 

# Comparison of non-linear solvers for FEM

This notebook researches different options for solving non linear systems of equations in the context of finite element methods. The system has the following form 

$$ \left( \begin{matrix} K_u & 0 \\ 0 & K_v \end{matrix}\right) \left( \begin{matrix} C_u \\ C_v \end{matrix} \right) - \left( \begin{matrix} f_u \\ f_v \end{matrix} \right)  + \left( \begin{matrix} \mathbf{H_u}(C_u, C_v) \\ \mathbf{H_v}(C_u, C_v) \end{matrix} \right) = \left( \begin{matrix} 0 \\ 0 \end{matrix} \right) $$

The objective is to have a solver which 

1. (efficient) is able to exploit the structure present in the problem (for example sparsity) 

2. (accurate) is stable for the pear problem

3. (user-friendly) can easily be implemented (libraries exist) in a compiled language

## Results

## The problem

We can interpret the equation to solve as consisting of a linear system with a non-linear right hand side. To simplify the analysis of the nonlinear system, we can divide our analysis in two steps: 

1. The linear matrix vector multiplication 

2. The nonlinearity

### The linear part 

Below are listed some properties and what we can expect about them 

1. Blocked: due to the two componenent structure of our system we have two non zero blocks $K_u$ and $K_v$. Exploiting this structure will improve memory usage by dismissing half of the matrix. 

2. Sparse: the integrals over the products of two chapeau functions are only non-zero whenever they share an edge. Therefor every row / column will only have three non-zero elements. 

3. Banded: by reordening the elements in the matrix we can expect the matrix to hava a banded structure. 

3. Non-symmetric: the pear-shaped domain doesn't show any symmetry to be exploited. 

4. Positive-definite: (to prove) the reaction diffusion equation likely gives rise to a positive definite system of equations. 

### The non-linear part

1. Shape of the non-linearity. The reaction terms introduce a non linearity, the interactive plots below show that the functions $R_u$ and $R_v$ are strictly decreasing with $c_u$ and $c_v$. 

2. Uniqueness of the solutions. This indicates that we might reasonably expect that the solution of the system is unique. The linear part can be interpreted as defining hyperplanes which intersect in a line through the origin. This line will only intersect the strictly decreasing non-linear part once. 

3. Shape of the Jacobian. The reaction terms only use information of the oxygen and carbon dioxide concentrations in the same gridpoint, therefor the Jacobian will have a block diagonal shape. 

In [1]:
using Plots; plotly(); 

Vᵐᵘ = 1
Kᵐᵘ = 1
Kᵐᵛ = 1
rᵘ = 1 
Vᵐᶠᵛ = 1
Kᵐᶠᵘ = 1

Rᵤ(cᵤ, cᵥ) = Vᵐᵘ*cᵤ/((Kᵐᵘ + cᵤ)*(1 + cᵥ/Kᵐᵛ));
Rᵥ(cᵤ, cᵥ) = rᵘ*Rᵤ(cᵤ, cᵥ) + Vᵐᶠᵛ/(1+cᵤ/Kᵐᶠᵘ); 

N = 200; a = 0.; b = 10.; 
cᵤ = a:(b-a)/N:b-1.0/N; 
cᵥ = a:(b-a)/N:b-1.0/N; 


display(plot(cᵤ, cᵥ, Rᵤ, st=:surface, title="Ru"))
display(plot(cᵤ, cᵥ, Rᵥ, st=:surface, title="Rv"))

<!DOCTYPE html>
 
 
 Plots.jl

<!DOCTYPE html>
 
 
 Plots.jl

In [2]:
d = 100
M = zeros(2*d, 2*d)
for i = 1:d
    M[i, i] = 2
    M[i, i+d] = 1
    M[i+d, i] = 1
    M[i+d, i+d] = 2
end
heatmap(M, title="Structure of Jacobian of the nonlinear part")

<!DOCTYPE html>
 
 
 Plots.jl

## Packages

This section introduces the packages used to illustrate the different methods

### JuliaNLSolvers

High level package to solve a non linear function given a function to calculate the residual and the jacobian. It implements three methods

1. Newton with line-search
2. Anderson
3. Trust-region


A simple example of the syntax is given in the listing below. 

```julia
using NLsolve

function f!(f, x)  
    ... # calculate residual
end
    
function j!(f, x)
    ... # calculate Jacobian
end

init_x = [ ... ]; 

nlsolve(f!, j!, init_x, method = :newton) 
```

### Optim

High level package to solve optimisation problems. It implements 

1. (L)BFGS
2. Conjugate Gradient
3. Newton
4. NelderMead
5. SimulatedAnnealing


The syntax is as follows

```julia 
using Optim

function o(x)
    ... # scalar objective function 
end

function f(x)
    ... # the system of equations
end

function j(x)
    ... # the jacobian of f
end

init_x = [ ... ]; 

# f and j are optional arguments 
res = optimize(o, f, j, init_x, method)


```

### LineSearches

This package implements different line search algorithms which can be given as methods to higher level solvers. The implemented line searches are

1. HagerZhang
2. MoreThuente
3. BackTracking
4. Strong Wolfe
5. Static

## Test problems

The code in this section creates three test cases

1. Dense matrix
2. Sparse matrix
3. Banded matrix

This allows to test how well the algorithms are able to exploit a specific structure. Most likely the matrix resulting from the discretisation will be sparse, having a lot of zeros. By reordening the numbering of the triangles in the discretisation it might be possible to create an almost banded structure. Having a structured matrix is beneficial since the linear solver can exploit it (e.g. Thomas algorithm for a tridiangular matrix). 

In [240]:
# dimensions
dᵤ = 100
dᵥ = 100

# vector f
fᵤ = randn(dᵤ); # provide problem data
fᵥ = randn(dᵥ); 
f = vcat(fᵤ, fᵥ); 

α = 1e-4; 

# non linear equations
mᵤ(cᵤ, cᵥ) = α*(-1/(cᵤ*cᵥ))
no_mᵤ(cᵤ, cᵥ) = -α; deno_mᵤ(cᵤ,cᵥ) = cᵤ*cᵥ;
mᵥ(cᵤ, cᵥ) = mᵤ(cᵤ, cᵥ) + α/cᵤ
no_mᵥ(cᵤ, cᵥ) = -α + α*cᵥ; deno_mᵥ(cᵤ, cᵥ) = cᵤ*cᵥ;
dmᵤdcᵤ(cᵤ, cᵥ) = α*1/cᵤ^2*1/cᵥ
dmᵤdcᵥ(cᵤ, cᵥ) = α*1/cᵥ^2*1/cᵤ
dmᵥdcᵤ(cᵤ, cᵥ) = dmᵤdcᵤ(cᵤ, cᵥ) - α*1/cᵤ^2
dmᵥdcᵥ(cᵤ, cᵥ) = dmᵤdcᵥ(cᵤ, cᵥ)

function h(x); 
    return vcat(mᵤ.(x[1:dᵤ], x[dᵤ+1:end]), mᵥ.(x[1:dᵤ], x[dᵤ+1:end]))
end



h (generic function with 1 method)

#### Dense matrix

In [241]:
using NLsolve, Random, Plots, LinearAlgebra

Kᵤ = randn(dᵤ, dᵤ); # provide problem data 
Kᵥ = randn(dᵥ, dᵥ);

# matrix A
A = zeros(dᵤ+dᵥ, dᵤ+dᵥ)
A[1:dᵤ, 1:dᵤ]         = Kᵤ; 
A[dᵤ+1:end, dᵤ+1:end] = Kᵥ; 

init_x = A \f; 

function ax_full(x);  
    return A*x; # able to exploit (sparse) structure here! 
end

function f_full(x) 
    return  ax_full(x) - f + h(x);
end

function f_full!(F, x) 
    F[1:end] = ax_full(x) - f + h(x);
end

M = zeros(size(A))

function j_full(x)
    fill!(M, 0.0)
    for i = 1:dᵤ
        M[i, i] = dmᵤdcᵤ(x[i], x[i+dᵤ])
        M[i, i+dᵤ] = dmᵥdcᵤ(x[i], x[i+dᵤ])
        M[i+dᵤ, i] = dmᵤdcᵥ(x[i], x[i+dᵤ])
        M[i+dᵤ, i+dᵤ] = dmᵥdcᵥ(x[i], x[i+dᵤ])
    end
    return M + A
end

function j_full!(J, x)
    fill!(J, 0.0)
    for i = 1:dᵤ
        J[i, i] = dmᵤdcᵤ(x[i], x[i+dᵤ])
        J[i, i+dᵤ] = dmᵥdcᵤ(x[i], x[i+dᵤ])
        J[i+dᵤ, i] = dmᵤdcᵥ(x[i], x[i+dᵤ])
        J[i+dᵤ, i+dᵤ] = dmᵥdcᵥ(x[i], x[i+dᵤ])
    end
    J[1:end, 1:end] = J[1:end, 1:end] + A
end;

#### Banded matrix

In [242]:
using BandedMatrices
using SparseArrays

Kᵤ = BandedMatrix((-1=>-2*ones(dᵤ-1), 0=>4*ones(dᵤ), 1=>-2*ones(dᵤ-1)), (dᵤ, dᵤ)); 

Kᵥ = BandedMatrix((-1=>-2*ones(dᵤ-1), 0=>4*ones(dᵤ), 1=>-2*ones(dᵤ-1)), (dᵤ, dᵤ)); 

A = BandedMatrix((-1=>-2*vcat(ones(dᵤ-1), [0], ones(dᵥ-1)), 0=>4*ones(dᵤ+dᵥ), 1=>-2*vcat(ones(dᵤ-1), [0], ones(dᵥ-1))), (dᵤ+dᵥ, dᵤ+dᵥ));

function ax_band(x);  
    return vcat(Kᵤ*x[1:dᵤ], Kᵥ*x[dᵤ+1:end])
end

function f_band(x) 
    return ax_band(x) - f + h(x);
end

function f_band!(F, x) 
    F[1:end] = ax_band(x) - f + h(x);
end

J_(x) = BandedMatrix((0=>vcat(dmᵤdcᵤ.(x[1:dᵤ], x[dᵤ+1:end]),dmᵥdcᵥ.(x[1:dᵤ], x[dᵤ+1:end])),
        dᵤ=>dmᵥdcᵤ.(x[1:dᵤ], x[dᵤ+1:end]),
        -dᵤ=>dmᵤdcᵥ.(x[1:dᵤ], x[dᵤ+1:end])), (dᵤ+dᵥ, dᵤ+dᵥ))

function j_band(x)
    return A + J_(x)
end

function j_band!(J, x)
    J[1:end, 1:end] = A + J_(x)
end;

## Methods

The system is non-linear, to solve it most algorithms will linearize it in some way. Therefor we can for analysis purposes divide the search for the algorithm in two parts:

   1. The linearisation scheme 
   2. The linear system solver

### Linearisation scheme

In [243]:
print_output(name, res, f) = println("""
    - problem type: $(name)
    - method: $(res.method)
    - iterations: $(res.iterations)
    - function calls: $(res.f_calls)
    - jacobian calls: $(res.g_calls)
    - inf norm residual: $(maximum(f(res.zero)))
""");

#### Newton

##### The method

The newton method solves $f(\mathbf{x}) = \mathbf{0}$ by using the first order taylor expansion arount a point $\mathbf{x_0}$

$$f(\mathbf{x_0+x}) = f(\mathbf{x_0}) + \nabla f(\mathbf{x_0})\mathbf{x} + O(\|\mathbf{x}\|^2). $$

The first order model is than solved for $f(\mathbf{x_0+x}) = 0$, 

$$  \nabla f(\mathbf{x_0})\mathbf{x} = - f(\mathbf{x_0}) $$

which results in a linear system of equations to be solved in each iteration. 

##### Line search 

When we define $f(\mathbf{x}) = \nabla g(\mathbf{x})$ with $g$ a scalar function, we can interpret Newton's method as using a second order model to find an extremum of the objective function $g$. The value of $\mathbf{x}$ found in each iteration step than corresponds to a search direction which uses second order information. This raises the idea to use line search methods to improve convergence of Newton's method. 

In [244]:
@time res = nlsolve(f_band, j_band, init_x, method = :newton); 

print_output("band", res, f_band)

@time res = nlsolve(f_full, j_full, init_x, method = :newton); 

print_output("full", res, f_full)

  0.429696 seconds (597.69 k allocations: 32.341 MiB, 5.23% gc time)
    - problem type: band
    - method: Newton with line-search
    - iterations: 4
    - function calls: 5
    - jacobian calls: 4
    - inf norm residual: 1.2486089038513028e-10

  0.041972 seconds (39.89 k allocations: 4.658 MiB)
    - problem type: full
    - method: Newton with line-search
    - iterations: 4
    - function calls: 5
    - jacobian calls: 4
    - inf norm residual: 1.2486089038513028e-10



#### BFGS

This is a class of Newton methods which uses an easier update for the Jacobian matrix, which allows to introduce additional conditions. The BFGS update formula is

$$B_{k+1} = B_k - \frac{B_k\mathbf{x_kx_k}^TB_k}{\mathbf{x_k}^TB_k\mathbf{x_k}} - \frac{f(\mathbf{x_k})f(\mathbf{x_k})^T}{f(\mathbf{x_k})^Ts_k}$$

and it guarantees a PD Jacobian in the case that the initial approximation is PD and $f(\mathbf{x_k})^T\mathbf{x_k}<0$. Improved performance is possible by immediately updating the inverse of the Jacobian matrix. 

Initial tests indicate that this works well with the strong Wolfe line search conditions

In [245]:
using Optim, LineSearches

function o_band(x)
    return x'*f_band(x)
end

function o_full(x)
    return x'*f_full(x)
end

println("Banded matrix")
@time res = optimize(o_band, f_band!, j_band!, init_x, LBFGS(linesearch = LineSearches.StrongWolfe()));
flush(stdout); display(res); flush(stdout); println(" ")

println("Dense matrix")
@time res = optimize(o_full, f_full!, j_full!, init_x, LBFGS(linesearch = LineSearches.StrongWolfe()));
flush(stdout); display(res); flush(stdout); println(" ")

Banded matrix
  0.093609 seconds (513.21 k allocations: 19.159 MiB, 40.36% gc time)


 * Status: failure (objective increased between iterations) (line search failed)

 * Candidate solution
    Minimizer: [-4.25e-01, -7.48e-01, -2.99e-01,  ...]
    Minimum:   -1.236148e+02

 * Found with
    Algorithm:     L-BFGS
    Initial Point: [1.40e+00, -1.84e-01, -2.18e+00,  ...]

 * Convergence measures
    |x - x'|               = 1.26e-06 ≰ 0.0e+00
    |x - x'|/|x'|          = 4.54e-08 ≰ 0.0e+00
    |f(x) - f(x')|         = 8.82e-08 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 7.13e-10 ≰ 0.0e+00
    |g(x)|                 = 1.14e+00 ≰ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    40
    f(x) calls:    392
    ∇f(x) calls:   265


 
Dense matrix
  0.057735 seconds (506.64 k allocations: 16.803 MiB, 12.16% gc time)


 * Status: failure (objective increased between iterations) (line search failed)

 * Candidate solution
    Minimizer: [-4.25e-01, -7.48e-01, -2.99e-01,  ...]
    Minimum:   -1.236148e+02

 * Found with
    Algorithm:     L-BFGS
    Initial Point: [1.40e+00, -1.84e-01, -2.18e+00,  ...]

 * Convergence measures
    |x - x'|               = 1.26e-06 ≰ 0.0e+00
    |x - x'|/|x'|          = 4.54e-08 ≰ 0.0e+00
    |f(x) - f(x')|         = 8.82e-08 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 7.13e-10 ≰ 0.0e+00
    |g(x)|                 = 1.14e+00 ≰ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    40
    f(x) calls:    392
    ∇f(x) calls:   265


#### Conjugate Gradient

This method calculates updates to $\mathbf{x_k}$ such that the updates are conjugate to each other. 

$$\mathbf{x_{k+1}-x_{k}} = - f(\mathbf{x_k}) + \beta_k (\mathbf{x_k-x_{k-1}})$$

In [246]:
function o_band(x)
    return x'*f_band(x)
end

function o_full(x)
    return x'*f_full(x)
end

println("Banded matrix")
@time begin; res = optimize(o_band, f_band!, j_band!, init_x, ConjugateGradient(linesearch=LineSearches.StrongWolfe())); end; 
flush(stdout); display(res); flush(stdout); println(" ")

println("Dense matrix")
t = @time begin; res = optimize(o_full, f_full!, j_full!, init_x, ConjugateGradient(linesearch=LineSearches.StrongWolfe())); end; 
flush(stdout); display(res); flush(stdout); println(" ")

Banded matrix
  0.021724 seconds (273.91 k allocations: 10.304 MiB)


 * Status: success

 * Candidate solution
    Minimizer: [-1.01e+00, -1.75e+00, -1.95e+00,  ...]
    Minimum:   -2.314498e+02

 * Found with
    Algorithm:     Conjugate Gradient
    Initial Point: [1.40e+00, -1.84e-01, -2.18e+00,  ...]

 * Convergence measures
    |x - x'|               = 0.00e+00 ≤ 0.0e+00
    |x - x'|/|x'|          = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|         = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 0.00e+00 ≤ 0.0e+00
    |g(x)|                 = 3.37e+01 ≰ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    31
    f(x) calls:    205
    ∇f(x) calls:   144


 
Dense matrix
  0.051012 seconds (270.42 k allocations: 9.053 MiB, 18.00% gc time)


 * Status: success

 * Candidate solution
    Minimizer: [-1.01e+00, -1.75e+00, -1.95e+00,  ...]
    Minimum:   -2.314498e+02

 * Found with
    Algorithm:     Conjugate Gradient
    Initial Point: [1.40e+00, -1.84e-01, -2.18e+00,  ...]

 * Convergence measures
    |x - x'|               = 0.00e+00 ≤ 0.0e+00
    |x - x'|/|x'|          = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|         = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 0.00e+00 ≤ 0.0e+00
    |g(x)|                 = 3.37e+01 ≰ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    31
    f(x) calls:    205
    ∇f(x) calls:   144


#### Newton with trust region 

Trust region methods limit the update step to have a bound on the norm, $\|\mathbf{x_{k+1}}-\mathbf{x_k}\|^2 \leq \Delta_k$. 

##### Benefits 

- 
- 

##### Downsides 

In [247]:
function o_band(x)
    return sum(f_band(x).^2)
end

function o_full(x)
    return sum(f_full(x).^2)
end



println("Banded matrix")
t = @time res = optimize(o_band, f_band!, j_band!, init_x, NewtonTrustRegion());
flush(stdout); display(res); flush(stdout); println(" ")

println("Dense matrix")
@time res = optimize(o_full, f_full!, j_full!, init_x, NewtonTrustRegion());
flush(stdout); display(res); flush(stdout); println(" ")

Banded matrix
  0.741332 seconds (154.51 k allocations: 217.602 MiB, 7.66% gc time)


 * Status: success

 * Candidate solution
    Minimizer: [-8.21e-01, -1.37e+00, -1.38e+00,  ...]
    Minimum:   3.728024e+00

 * Found with
    Algorithm:     Newton's Method (Trust Region)
    Initial Point: [1.40e+00, -1.84e-01, -2.18e+00,  ...]

 * Convergence measures
    |x - x'|               = 0.00e+00 ≤ 0.0e+00
    |x - x'|/|x'|          = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|         = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 0.00e+00 ≤ 0.0e+00
    |g(x)|                 = 2.92e-01 ≰ 1.0e-08

 * Work counters
    Seconds run:   1  (vs limit Inf)
    Iterations:    41
    f(x) calls:    42
    ∇f(x) calls:   42
    ∇²f(x) calls:  14


 
Dense matrix
  0.732179 seconds (177.45 k allocations: 217.796 MiB, 6.43% gc time)


 * Status: success

 * Candidate solution
    Minimizer: [-8.21e-01, -1.37e+00, -1.38e+00,  ...]
    Minimum:   3.728024e+00

 * Found with
    Algorithm:     Newton's Method (Trust Region)
    Initial Point: [1.40e+00, -1.84e-01, -2.18e+00,  ...]

 * Convergence measures
    |x - x'|               = 0.00e+00 ≤ 0.0e+00
    |x - x'|/|x'|          = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|         = 0.00e+00 ≤ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 0.00e+00 ≤ 0.0e+00
    |g(x)|                 = 2.92e-01 ≰ 1.0e-08

 * Work counters
    Seconds run:   1  (vs limit Inf)
    Iterations:    41
    f(x) calls:    42
    ∇f(x) calls:   42
    ∇²f(x) calls:  14


#### Homotopy

Since we expect that there is only one solutions, a homotopy method needs only to track one path. The code below starts from the solution of the linear system and slowly introduces the non linearity while tracking the solution of the system. 


##### Benefits

- Expected that convergence can be proved


##### Downsides

- Complex algorithm, difficult to optimize (e.g. inverse of jacobian) for our specific case


In [248]:
using HomotopyContinuation, DynamicPolynomials

@polyvar cᵤᵥ[1:dᵤ] cᵥᵥ[1:dᵥ] t

γ = randn(ComplexF64)

init_sol = A \ f;  


P = zeros(Polynomial{true, ComplexF64}, dᵤ + dᵥ)
Q = zeros(Polynomial{true, ComplexF64}, dᵤ + dᵥ)
for i ∈ 1:dᵤ
    P[i] = A[i, :]'*vcat(cᵤᵥ, cᵥᵥ)*deno_mᵤ(cᵤᵥ[i], cᵥᵥ[i]) + no_mᵤ(cᵤᵥ[i], cᵥᵥ[i]) - fᵤ[i]*deno_mᵤ(cᵤᵥ[i], cᵥᵥ[i]);
    P[i+dᵤ] = A[i+dᵤ, :]'*vcat(cᵤᵥ, cᵥᵥ)*deno_mᵥ(cᵤᵥ[i], cᵥᵥ[i]) + no_mᵥ(cᵤᵥ[i], cᵥᵥ[i]) - fᵥ[i]*deno_mᵥ(cᵤᵥ[i], cᵥᵥ[i]);
    
    Q[i] = A[i, :]'*vcat(cᵤᵥ, cᵥᵥ)- fᵤ[i]; 
    Q[i+dᵤ] = A[i+dᵤ, :]'*vcat(cᵤᵥ, cᵥᵥ)- fᵥ[i]; 
end

res = HomotopyContinuation.solve(Q, P, [init_sol])

@time res = HomotopyContinuation.solve(Q, P, [init_sol])


InterruptException: InterruptException:

In [238]:
println(sum([P[i]([cᵤᵥ; cᵥᵥ]=>solutions(res)[1]) for i ∈ 1:dᵤ+dᵥ]))
println(sum(f_full(solutions(res)[1])))

MethodError: MethodError: no method matching solutions(::Optim.MultivariateOptimizationResults{ConjugateGradient{Float64,Nothing,getfield(Optim, Symbol("##31#33")),InitialHagerZhang{Float64},StrongWolfe{Float64}},Float64,Array{Float64,1},Float64,Float64,Array{OptimizationState{Float64,ConjugateGradient{Float64,Nothing,getfield(Optim, Symbol("##31#33")),InitialHagerZhang{Float64},StrongWolfe{Float64}}},1},Bool})
Closest candidates are:
  solutions(!Matched::Union{Array{#s591,1} where #s591<:PathResult, Result}; kwargs...) at /Users/ronald/.juliapro/JuliaPro_v1.1.1.1/packages/HomotopyContinuation/EYtCe/src/solve.jl:797
  solutions(!Matched::HomotopyContinuation.Loop) at /Users/ronald/.juliapro/JuliaPro_v1.1.1.1/packages/HomotopyContinuation/EYtCe/src/monodromy.jl:270
  solutions(!Matched::MonodromyResult; kwargs...) at /Users/ronald/.juliapro/JuliaPro_v1.1.1.1/packages/HomotopyContinuation/EYtCe/src/monodromy.jl:480

#### Anderson

This method proves to be unstable for our problem. 

In [239]:
@time res = nlsolve(f_band, j_band, init_x, method = :anderson); 

print_output("band", res, f_band)

@time res = nlsolve(f_full, j_full, init_x, method = :anderson); 

print_output("full", res, f_full)

  0.603276 seconds (8.02 M allocations: 322.726 MiB, 45.78% gc time)
    - problem type: band
    - method: Anderson m=0 beta=1 aa_start=1 droptol=0
    - iterations: 1000
    - function calls: 1000
    - jacobian calls: 0
    - inf norm residual: NaN

  0.616729 seconds (8.01 M allocations: 291.537 MiB, 48.89% gc time)
    - problem type: full
    - method: Anderson m=0 beta=1 aa_start=1 droptol=0
    - iterations: 1000
    - function calls: 1000
    - jacobian calls: 0
    - inf norm residual: NaN



#### Trust-region

Explain trust region

In [9]:
@time res = nlsolve(f_band, j_band, init_x, method = :trust_region); 

print_output("band", res, f_band)

@time res = nlsolve(f_full, j_full, init_x, method = :trust_region); 

print_output("full", res, f_full)

  2.152144 seconds (400.68 k allocations: 956.145 MiB, 12.59% gc time)
    - problem type: band
    - method: Trust-region with dogleg and autoscaling
    - iterations: 9
    - function calls: 10
    - jacobian calls: 10
    - inf norm residual: 2.2953229991614792e-11

  1.650579 seconds (560.02 k allocations: 651.845 MiB, 18.98% gc time)
    - problem type: full
    - method: Trust-region with dogleg and autoscaling
    - iterations: 9
    - function calls: 10
    - jacobian calls: 10
    - inf norm residual: 2.2953229991614792e-11



### Linear solver

## Availability in C++

http://eigen.tuxfamily.org/index.php?title=Main_Page#Documentation

## Various

Banded matrix multiplication can be 300 times faster. 

In [32]:
# set dimension 
d = 10000; 

x = randn(d); 

# generate full and banded matrix
A = zeros(d, d); 
for i ∈ 1:d
    A[i, i] = 4; 
    if i > 1 && i < d; A[i-1, i] = -2; A[i, i-1] = -2; end
end

B = BandedMatrix((-1=>-2*ones(d-1), 0=>4*ones(d), 1=>-2*ones(d-1)), (d, d));

b = zeros(d) # store solution, otherwise compiler might shortcut

println("full matrix")

# warm-up
for i ∈ 1:10; b += A*x; end

@time for i ∈ 1:50; b = A*x; end; 

b = zeros(d)

println("banded matrix")

# warm-up 
for i ∈ 1:10; b += B*x; end; 

@time for i ∈ 1:50; b=B*x; end; 



full matrix
  4.065323 seconds (100 allocations: 3.819 MiB)
banded matrix
  0.008891 seconds (300 allocations: 3.824 MiB)
